#Evaluating Risk for Loan Approvals

### Notebook Objectives
1. Build a predictive model that estimates the probability individual loans will default.
2. Identify the loan cutoff rate that maximixes profits.
3. Use real-world lending data to identify and rank which features make a loan most at-risk.
 
### Notebook Oberview
<a href="https://ibb.co/cuQYr6"><img src="https://preview.ibb.co/jNxPym/Image.png" alt="Image" border="0"></a>

## The Data

The data used is public data from the peer-ro-peer lenidng platform [LendingClub](https://en.wikipedia.org/wiki/LendingClub). It includes all funded loans from 2007 to 2018. Each loan includes applicant information provided by the applicant as well as the current loan status (Current, Late, Fully Paid, etc.) and latest payment information. For a full view of the data please view the data dictionary available [here](https://resources.lendingclub.com/LCDataDictionary.xlsx).


![Loan_Data](https://preview.ibb.co/d3tQ4R/Screen_Shot_2018_02_02_at_11_21_51_PM.png)

In [3]:
loan_stats = spark.table("lendingclub_accepted")
print(str(loan_stats.count()) + " loans opened by Lending Club...")

2260701 loans opened by Lending Club...

In [4]:
display(loan_stats)

id member_id loan_amnt funded_amnt funded_amnt_inv term int_rate installment grade sub_grade emp_title emp_length home_ownership annual_inc verification_status issue_d loan_status pymnt_plan url desc purpose title zip_code addr_state dti delinq_2yrs earliest_cr_line fico_range_low fico_range_high inq_last_6mths mths_since_last_delinq mths_since_last_record open_acc pub_rec revol_bal revol_util total_acc initial_list_status out_prncp out_prncp_inv total_pymnt total_pymnt_inv total_rec_prncp total_rec_int total_rec_late_fee recoveries collection_recovery_fee last_pymnt_d last_pymnt_amnt next_pymnt_d last_credit_pull_d last_fico_range_high last_fico_range_low collections_12_mths_ex_med mths_since_last_major_derog policy_code application_type annual_inc_joint dti_joint verification_status_joint acc_now_delinq tot_coll_amt tot_cur_bal open_acc_6m open_act_il open_il_12m open_il_24m mths_since_rcnt_il total_bal_il il_util open_rv_12m open_rv_24m max_bal_bc all_util total_rev_hi_lim inq_fi total_cu_tl inq_last_12m acc_open_past_24mths avg_cur_bal bc_open_to_buy bc_util chargeoff_within_12_mths delinq_amnt mo_sin_old_il_acct mo_sin_old_rev_tl_op mo_sin_rcnt_rev_tl_op mo_sin_rcnt_tl mort_acc mths_since_recent_bc mths_since_recent_bc_dlq mths_since_recent_inq mths_since_recent_revol_delinq num_accts_ever_120_pd num_actv_bc_tl num_actv_rev_tl num_bc_sats num_bc_tl num_il_tl num_op_rev_tl num_rev_accts num_rev_tl_bal_gt_0 num_sats num_tl_120dpd_2m num_tl_30dpd num_tl_90g_dpd_24m num_tl_op_past_12m pct_tl_nvr_dlq percent_bc_gt_75 pub_rec_bankruptcies tax_liens tot_hi_cred_lim total_bal_ex_mort total_bc_limit total_il_high_credit_limit revol_bal_joint sec_app_fico_range_low sec_app_fico_range_high sec_app_earliest_cr_line sec_app_inq_last_6mths sec_app_mort_acc sec_app_open_acc sec_app_revol_util sec_app_open_act_il sec_app_num_rev_accts sec_app_chargeoff_within_12_mths sec_app_collections_12_mths_ex_med sec_app_mths_since_last_major_derog hardship_flag hardship_type hardship_reason hardship_status deferral_term hardship_amount hardship_start_date hardship_end_date payment_plan_start_date hardship_length hardship_dpd hardship_loan_status orig_projected_additional_accrued_interest hardship_payoff_balance_amount hardship_last_payment_amount disbursement_method debt_settlement_flag debt_settlement_flag_date settlement_status settlement_date settlement_amount settlement_percentage settlement_term 68407277 null 3600.0 3600.0 3600.0 36 months 13.99 123.03 C C4 leadman 10+ years MORTGAGE 55000.0 Not Verified Dec-2015 Fully Paid n https://lendingclub.com/browse/loanDetail.action?loan_id=68407277 null debt_consolidation Debt consolidation 190xx PA 5.91 0.0 Aug-2003 675.0 679.0 1.0 30.0 null 7.0 0.0 2765.0 29.7 13.0 w 0.0 0.0 4421.723916800001 4421.72 3600.0 821.72 0.0 0.0 0.0 Jan-2019 122.67 null Mar-2019 564.0 560.0 0.0 30.0 1.0 Individual null null null 0.0 722.0 144904.0 2.0 2.0 0.0 1.0 21.0 4981.0 36.0 3.0 3.0 722.0 34.0 9300.0 3.0 1.0 4.0 4.0 20701.0 1506.0 37.2 0.0 0.0 148.0 128.0 3.0 3.0 1.0 4.0 69.0 4.0 69.0 2.0 2.0 4.0 2.0 5.0 3.0 4.0 9.0 4.0 7.0 0.0 0.0 0.0 3.0 76.9 0.0 0.0 0.0 178050.0 7746.0 2400.0 13734.0 null null null null null null null null null null null null null N null null null null null null null null null null null null null null Cash N null null null null null null 68355089 null 24700.0 24700.0 24700.0 36 months 11.99 820.28 C C1 Engineer 10+ years MORTGAGE 65000.0 Not Verified Dec-2015 Fully Paid n https://lendingclub.com/browse/loanDetail.action?loan_id=68355089 null small_business Business 577xx SD 16.06 1.0 Dec-1999 715.0 719.0 4.0 6.0 null 22.0 0.0 21470.0 19.2 38.0 w 0.0 0.0 25679.66 25679.66 24700.0 979.66 0.0 0.0 0.0 Jun-2016 926.35 null Mar-2019 699.0 695.0 0.0 null 1.0 Individual null null null 0.0 0.0 204396.0 1.0 1.0 0.0 1.0 19.0 18005.0 73.0 2.0 3.0 6472.0 29.0 111800.0 0.0 0.0 6.0 4.0 9733.0 57830.0 27.1 0.0 0.0 113.0 192.0 2.0 2.0 4.0 2.0 null 0.0 6.0 0.0 5.0 5.0 13.0 17.0 6.0 20.0 27.0 5.0 22.0 0.0 0.0 0.0 2.0

In [5]:
# Loans are assigned a letter grade from 'A' to 'G' with 'A' being the best
display(loan_stats)

id member_id loan_amnt funded_amnt funded_amnt_inv term int_rate installment grade sub_grade emp_title emp_length home_ownership annual_inc verification_status issue_d loan_status pymnt_plan url desc purpose title zip_code addr_state dti delinq_2yrs earliest_cr_line fico_range_low fico_range_high inq_last_6mths mths_since_last_delinq mths_since_last_record open_acc pub_rec revol_bal revol_util total_acc initial_list_status out_prncp out_prncp_inv total_pymnt total_pymnt_inv total_rec_prncp total_rec_int total_rec_late_fee recoveries collection_recovery_fee last_pymnt_d last_pymnt_amnt next_pymnt_d last_credit_pull_d last_fico_range_high last_fico_range_low collections_12_mths_ex_med mths_since_last_major_derog policy_code application_type annual_inc_joint dti_joint verification_status_joint acc_now_delinq tot_coll_amt tot_cur_bal open_acc_6m open_act_il open_il_12m open_il_24m mths_since_rcnt_il total_bal_il il_util open_rv_12m open_rv_24m max_bal_bc all_util total_rev_hi_lim inq_fi total_cu_tl inq_last_12m acc_open_past_24mths avg_cur_bal bc_open_to_buy bc_util chargeoff_within_12_mths delinq_amnt mo_sin_old_il_acct mo_sin_old_rev_tl_op mo_sin_rcnt_rev_tl_op mo_sin_rcnt_tl mort_acc mths_since_recent_bc mths_since_recent_bc_dlq mths_since_recent_inq mths_since_recent_revol_delinq num_accts_ever_120_pd num_actv_bc_tl num_actv_rev_tl num_bc_sats num_bc_tl num_il_tl num_op_rev_tl num_rev_accts num_rev_tl_bal_gt_0 num_sats num_tl_120dpd_2m num_tl_30dpd num_tl_90g_dpd_24m num_tl_op_past_12m pct_tl_nvr_dlq percent_bc_gt_75 pub_rec_bankruptcies tax_liens tot_hi_cred_lim total_bal_ex_mort total_bc_limit total_il_high_credit_limit revol_bal_joint sec_app_fico_range_low sec_app_fico_range_high sec_app_earliest_cr_line sec_app_inq_last_6mths sec_app_mort_acc sec_app_open_acc sec_app_revol_util sec_app_open_act_il sec_app_num_rev_accts sec_app_chargeoff_within_12_mths sec_app_collections_12_mths_ex_med sec_app_mths_since_last_major_derog hardship_flag hardship_type hardship_reason hardship_status deferral_term hardship_amount hardship_start_date hardship_end_date payment_plan_start_date hardship_length hardship_dpd hardship_loan_status orig_projected_additional_accrued_interest hardship_payoff_balance_amount hardship_last_payment_amount disbursement_method debt_settlement_flag debt_settlement_flag_date settlement_status settlement_date settlement_amount settlement_percentage settlement_term 68407277 null 3600.0 3600.0 3600.0 36 months 13.99 123.03 C C4 leadman 10+ years MORTGAGE 55000.0 Not Verified Dec-2015 Fully Paid n https://lendingclub.com/browse/loanDetail.action?loan_id=68407277 null debt_consolidation Debt consolidation 190xx PA 5.91 0.0 Aug-2003 675.0 679.0 1.0 30.0 null 7.0 0.0 2765.0 29.7 13.0 w 0.0 0.0 4421.723916800001 4421.72 3600.0 821.72 0.0 0.0 0.0 Jan-2019 122.67 null Mar-2019 564.0 560.0 0.0 30.0 1.0 Individual null null null 0.0 722.0 144904.0 2.0 2.0 0.0 1.0 21.0 4981.0 36.0 3.0 3.0 722.0 34.0 9300.0 3.0 1.0 4.0 4.0 20701.0 1506.0 37.2 0.0 0.0 148.0 128.0 3.0 3.0 1.0 4.0 69.0 4.0 69.0 2.0 2.0 4.0 2.0 5.0 3.0 4.0 9.0 4.0 7.0 0.0 0.0 0.0 3.0 76.9 0.0 0.0 0.0 178050.0 7746.0 2400.0 13734.0 null null null null null null null null null null null null null N null null null null null null null null null null null null null null Cash N null null null null null null 68355089 null 24700.0 24700.0 24700.0 36 months 11.99 820.28 C C1 Engineer 10+ years MORTGAGE 65000.0 Not Verified Dec-2015 Fully Paid n https://lendingclub.com/browse/loanDetail.action?loan_id=68355089 null small_business Business 577xx SD 16.06 1.0 Dec-1999 715.0 719.0 4.0 6.0 null 22.0 0.0 21470.0 19.2 38.0 w 0.0 0.0 25679.66 25679.66 24700.0 979.66 0.0 0.0 0.0 Jun-2016 926.35 null Mar-2019 699.0 695.0 0.0 null 1.0 Individual null null null 0.0 0.0 204396.0 1.0 1.0 0.0 1.0 19.0 18005.0 73.0 2.0 3.0 6472.0 29.0 111800.0 0.0 0.0 6.0 4.0 9733.0 57830.0 27.1 0.0 0.0 113.0 192.0 2.0 2.0 4.0 2.0 null 0.0 6.0 0.0 5.0 5.0 13.0 17.0 6.0 20.0 27.0 5.0 22.0 0.0 0.0 0.0 2.0

In [6]:
from pyspark.sql.functions import *

print("------------------------------------------------------------------------------------------------")
print("Create bad loan label, this will include charged off, defaulted, and late repayments on loans...")
loan_stats = loan_stats.filter(loan_stats.loan_status.isin(["Default", "Charged Off", "Fully Paid"]))\
                       .withColumn("bad_loan", (~(loan_stats.loan_status == "Fully Paid")).cast("string"))

print("------------------------------------------------------------------------------------------------")
print("Turning string interest rate and revoling util columns into numeric columns...")
loan_stats = loan_stats.withColumn('int_rate', regexp_replace('int_rate', '%', '').cast('float')) \
                       .withColumn('revol_util', regexp_replace('revol_util', '%', '').cast('float')) \
                       .withColumn('issue_year',  substring(loan_stats.issue_d, 5, 4).cast('double') ) \
                       .withColumn('earliest_year', substring(loan_stats.earliest_cr_line, 5, 4).cast('double'))
loan_stats = loan_stats.withColumn('credit_length_in_years', (loan_stats.issue_year - loan_stats.earliest_year))

print("------------------------------------------------------------------------------------------------")
print("Turning remaining string columns into numeric columns...")
loan_stats = loan_stats.withColumn('annual_inc', loan_stats.annual_inc.cast('float')) \
                       .withColumn('dti', loan_stats.dti.cast('float')) \
                       .withColumn('total_acc', loan_stats.total_acc.cast('double') ) \
                       .withColumn('delinq_2yrs', loan_stats.delinq_2yrs.cast('double'))

print("------------------------------------------------------------------------------------------------")
print("Converting emp_length column into numeric...")
loan_stats = loan_stats.withColumn('emp_length', trim(regexp_replace(loan_stats.emp_length, "([ ]*+[a-zA-Z].*)|(n/a)", "") ))
loan_stats = loan_stats.withColumn('emp_length', trim(regexp_replace(loan_stats.emp_length, "< 1", "0") ))
loan_stats = loan_stats.withColumn('emp_length', trim(regexp_replace(loan_stats.emp_length, "10\\+", "10") ).cast('float'))

print("------------------------------------------------------------------------------------------------")
print("Map multiple levels into one factor level for verification_status...")
loan_stats = loan_stats.withColumn('verification_status', trim(regexp_replace(loan_stats.verification_status, 'Source Verified', 'Verified')))

print("------------------------------------------------------------------------------------------------")
print("Calculate the total amount of money earned or lost per loan...")
loan_stats = loan_stats.withColumn('net', round( loan_stats.total_pymnt - loan_stats.loan_amnt, 2))

print("------------------------------------------------------------------------------------------------")
print("Drop rows where state is not listed as a 2-letter code...")
loan_stats = loan_stats.filter(length(loan_stats.addr_state)==2)

------------------------------------------------------------------------------------------------
Create bad loan label, this will include charged off, defaulted, and late repayments on loans...
------------------------------------------------------------------------------------------------
Turning string interest rate and revoling util columns into numeric columns...
------------------------------------------------------------------------------------------------
Turning remaining string columns into numeric columns...
------------------------------------------------------------------------------------------------
Converting emp_length column into numeric...
------------------------------------------------------------------------------------------------
Map multiple levels into one factor level for verification_status...
------------------------------------------------------------------------------------------------
Calculate the total amount of money earned or lost per loan...
------------------------------------------------------------------------------------------------
Drop rows where state is not listed as a 2-letter code...

In [7]:
loan_stats.createOrReplaceTempView("loan_stats")

In [8]:
display(loan_stats)

id member_id loan_amnt funded_amnt funded_amnt_inv term int_rate installment grade sub_grade emp_title emp_length home_ownership annual_inc verification_status issue_d loan_status pymnt_plan url desc purpose title zip_code addr_state dti delinq_2yrs earliest_cr_line fico_range_low fico_range_high inq_last_6mths mths_since_last_delinq mths_since_last_record open_acc pub_rec revol_bal revol_util total_acc initial_list_status out_prncp out_prncp_inv total_pymnt total_pymnt_inv total_rec_prncp total_rec_int total_rec_late_fee recoveries collection_recovery_fee last_pymnt_d last_pymnt_amnt next_pymnt_d last_credit_pull_d last_fico_range_high last_fico_range_low collections_12_mths_ex_med mths_since_last_major_derog policy_code application_type annual_inc_joint dti_joint verification_status_joint acc_now_delinq tot_coll_amt tot_cur_bal open_acc_6m open_act_il open_il_12m open_il_24m mths_since_rcnt_il total_bal_il il_util open_rv_12m open_rv_24m max_bal_bc all_util total_rev_hi_lim inq_fi total_cu_tl inq_last_12m acc_open_past_24mths avg_cur_bal bc_open_to_buy bc_util chargeoff_within_12_mths delinq_amnt mo_sin_old_il_acct mo_sin_old_rev_tl_op mo_sin_rcnt_rev_tl_op mo_sin_rcnt_tl mort_acc mths_since_recent_bc mths_since_recent_bc_dlq mths_since_recent_inq mths_since_recent_revol_delinq num_accts_ever_120_pd num_actv_bc_tl num_actv_rev_tl num_bc_sats num_bc_tl num_il_tl num_op_rev_tl num_rev_accts num_rev_tl_bal_gt_0 num_sats num_tl_120dpd_2m num_tl_30dpd num_tl_90g_dpd_24m num_tl_op_past_12m pct_tl_nvr_dlq percent_bc_gt_75 pub_rec_bankruptcies tax_liens tot_hi_cred_lim total_bal_ex_mort total_bc_limit total_il_high_credit_limit revol_bal_joint sec_app_fico_range_low sec_app_fico_range_high sec_app_earliest_cr_line sec_app_inq_last_6mths sec_app_mort_acc sec_app_open_acc sec_app_revol_util sec_app_open_act_il sec_app_num_rev_accts sec_app_chargeoff_within_12_mths sec_app_collections_12_mths_ex_med sec_app_mths_since_last_major_derog hardship_flag hardship_type hardship_reason hardship_status deferral_term hardship_amount hardship_start_date hardship_end_date payment_plan_start_date hardship_length hardship_dpd hardship_loan_status orig_projected_additional_accrued_interest hardship_payoff_balance_amount hardship_last_payment_amount disbursement_method debt_settlement_flag debt_settlement_flag_date settlement_status settlement_date settlement_amount settlement_percentage settlement_term bad_loan issue_year earliest_year credit_length_in_years net 68407277 null 3600.0 3600.0 3600.0 36 months 13.99 123.03 C C4 leadman 10.0 MORTGAGE 55000.0 Not Verified Dec-2015 Fully Paid n https://lendingclub.com/browse/loanDetail.action?loan_id=68407277 null debt_consolidation Debt consolidation 190xx PA 5.91 0.0 Aug-2003 675.0 679.0 1.0 30.0 null 7.0 0.0 2765.0 29.7 13.0 w 0.0 0.0 4421.723916800001 4421.72 3600.0 821.72 0.0 0.0 0.0 Jan-2019 122.67 null Mar-2019 564.0 560.0 0.0 30.0 1.0 Individual null null null 0.0 722.0 144904.0 2.0 2.0 0.0 1.0 21.0 4981.0 36.0 3.0 3.0 722.0 34.0 9300.0 3.0 1.0 4.0 4.0 20701.0 1506.0 37.2 0.0 0.0 148.0 128.0 3.0 3.0 1.0 4.0 69.0 4.0 69.0 2.0 2.0 4.0 2.0 5.0 3.0 4.0 9.0 4.0 7.0 0.0 0.0 0.0 3.0 76.9 0.0 0.0 0.0 178050.0 7746.0 2400.0 13734.0 null null null null null null null null null null null null null N null null null null null null null null null null null null null null Cash N null null null null null null false 2015.0 2003.0 12.0 821.72 68355089 null 24700.0 24700.0 24700.0 36 months 11.99 820.28 C C1 Engineer 10.0 MORTGAGE 65000.0 Not Verified Dec-2015 Fully Paid n https://lendingclub.com/browse/loanDetail.action?loan_id=68355089 null small_business Business 577xx SD 16.06 1.0 Dec-1999 715.0 719.0 4.0 6.0 null 22.0 0.0 21470.0 19.2 38.0 w 0.0 0.0 25679.66 25679.66 24700.0 979.66 0.0 0.0 0.0 Jun-2016 926.35 null Mar-2019 699.0 695.0 0.0 null 1.0 Individual null null null 0.0 0.0 204396.0 1.0 1.0 0.0 1.0 19.0 18005.0 73.0 2.0 3.0 6472.0 29.0 111800.0 0.0 0.0 6.0 4.0 9733.0 57830.0 27.1 0.0 0.0 113.0 192.0 2.0 2.

In [9]:
display(loan_stats.groupBy("addr_state").agg((count(col("annual_inc"))).alias("ratio")))

addr_state ratio SC 15992 AZ 32689 LA 15498 MN 23964 NJ 48441 DC 3474 OR 16410 VA 38030 RI 5872 WY 2921 KY 12838 NH 6448 MI 35228 NV 20263 WI 17728 ID 1689 CA 196483 CT 19726 NE 3586 MT 3822 NC 37785 VT 2652 MD 31220 DE 3781 MO 21260 IL 51706 ME 2029 WA 29182 ND 1602 MS 6587 AL 16612 IN 21716 OH 43839 TN 20385 NM 7361 IA 7 PA 45516 SD 2767 NY 109837 TX 110160 WV 4877 GA 43366 MA 30966 KS 11238 FL 95598 CO 29666 AK 3188 AR 10047 OK 12281 UT 10033 HI 6757

In [10]:
%sql
SELECT DISTINCT(issue_year), bad_loan, COUNT(DISTINCT(id))
FROM loan_stats
GROUP BY issue_year, bad_loan
ORDER BY issue_year, bad_loan

issue_year bad_loan count(DISTINCT id) 2007.0 false 205 2007.0 true 44 2008.0 false 1294 2008.0 true 241 2009.0 false 4026 2009.0 true 578 2010.0 false 9982 2010.0 true 1477 2011.0 false 18417 2011.0 true 3297 2012.0 false 44723 2012.0 true 8644 2013.0 false 113780 2013.0 true 21024 2014.0 false 181941 2014.0 true 41162 2015.0 false 299742 2015.0 true 75803 2016.0 false 224853 2016.0 true 68251 2017.0 false 130152 2017.0 true 39169 2018.0 false 47444 2018.0 true 8874

In [11]:
display(loan_stats)

id member_id loan_amnt funded_amnt funded_amnt_inv term int_rate installment grade sub_grade emp_title emp_length home_ownership annual_inc verification_status issue_d loan_status pymnt_plan url desc purpose title zip_code addr_state dti delinq_2yrs earliest_cr_line fico_range_low fico_range_high inq_last_6mths mths_since_last_delinq mths_since_last_record open_acc pub_rec revol_bal revol_util total_acc initial_list_status out_prncp out_prncp_inv total_pymnt total_pymnt_inv total_rec_prncp total_rec_int total_rec_late_fee recoveries collection_recovery_fee last_pymnt_d last_pymnt_amnt next_pymnt_d last_credit_pull_d last_fico_range_high last_fico_range_low collections_12_mths_ex_med mths_since_last_major_derog policy_code application_type annual_inc_joint dti_joint verification_status_joint acc_now_delinq tot_coll_amt tot_cur_bal open_acc_6m open_act_il open_il_12m open_il_24m mths_since_rcnt_il total_bal_il il_util open_rv_12m open_rv_24m max_bal_bc all_util total_rev_hi_lim inq_fi total_cu_tl inq_last_12m acc_open_past_24mths avg_cur_bal bc_open_to_buy bc_util chargeoff_within_12_mths delinq_amnt mo_sin_old_il_acct mo_sin_old_rev_tl_op mo_sin_rcnt_rev_tl_op mo_sin_rcnt_tl mort_acc mths_since_recent_bc mths_since_recent_bc_dlq mths_since_recent_inq mths_since_recent_revol_delinq num_accts_ever_120_pd num_actv_bc_tl num_actv_rev_tl num_bc_sats num_bc_tl num_il_tl num_op_rev_tl num_rev_accts num_rev_tl_bal_gt_0 num_sats num_tl_120dpd_2m num_tl_30dpd num_tl_90g_dpd_24m num_tl_op_past_12m pct_tl_nvr_dlq percent_bc_gt_75 pub_rec_bankruptcies tax_liens tot_hi_cred_lim total_bal_ex_mort total_bc_limit total_il_high_credit_limit revol_bal_joint sec_app_fico_range_low sec_app_fico_range_high sec_app_earliest_cr_line sec_app_inq_last_6mths sec_app_mort_acc sec_app_open_acc sec_app_revol_util sec_app_open_act_il sec_app_num_rev_accts sec_app_chargeoff_within_12_mths sec_app_collections_12_mths_ex_med sec_app_mths_since_last_major_derog hardship_flag hardship_type hardship_reason hardship_status deferral_term hardship_amount hardship_start_date hardship_end_date payment_plan_start_date hardship_length hardship_dpd hardship_loan_status orig_projected_additional_accrued_interest hardship_payoff_balance_amount hardship_last_payment_amount disbursement_method debt_settlement_flag debt_settlement_flag_date settlement_status settlement_date settlement_amount settlement_percentage settlement_term bad_loan issue_year earliest_year credit_length_in_years net 68407277 null 3600.0 3600.0 3600.0 36 months 13.99 123.03 C C4 leadman 10.0 MORTGAGE 55000.0 Not Verified Dec-2015 Fully Paid n https://lendingclub.com/browse/loanDetail.action?loan_id=68407277 null debt_consolidation Debt consolidation 190xx PA 5.91 0.0 Aug-2003 675.0 679.0 1.0 30.0 null 7.0 0.0 2765.0 29.7 13.0 w 0.0 0.0 4421.723916800001 4421.72 3600.0 821.72 0.0 0.0 0.0 Jan-2019 122.67 null Mar-2019 564.0 560.0 0.0 30.0 1.0 Individual null null null 0.0 722.0 144904.0 2.0 2.0 0.0 1.0 21.0 4981.0 36.0 3.0 3.0 722.0 34.0 9300.0 3.0 1.0 4.0 4.0 20701.0 1506.0 37.2 0.0 0.0 148.0 128.0 3.0 3.0 1.0 4.0 69.0 4.0 69.0 2.0 2.0 4.0 2.0 5.0 3.0 4.0 9.0 4.0 7.0 0.0 0.0 0.0 3.0 76.9 0.0 0.0 0.0 178050.0 7746.0 2400.0 13734.0 null null null null null null null null null null null null null N null null null null null null null null null null null null null null Cash N null null null null null null false 2015.0 2003.0 12.0 821.72 68355089 null 24700.0 24700.0 24700.0 36 months 11.99 820.28 C C1 Engineer 10.0 MORTGAGE 65000.0 Not Verified Dec-2015 Fully Paid n https://lendingclub.com/browse/loanDetail.action?loan_id=68355089 null small_business Business 577xx SD 16.06 1.0 Dec-1999 715.0 719.0 4.0 6.0 null 22.0 0.0 21470.0 19.2 38.0 w 0.0 0.0 25679.66 25679.66 24700.0 979.66 0.0 0.0 0.0 Jun-2016 926.35 null Mar-2019 699.0 695.0 0.0 null 1.0 Individual null null null 0.0 0.0 204396.0 1.0 1.0 0.0 1.0 19.0 18005.0 73.0 2.0 3.0 6472.0 29.0 111800.0 0.0 0.0 6.0 4.0 9733.0 57830.0 27.1 0.0 0.0 113.0 192.0 2.0 2.

In [12]:
from pyspark.ml import Pipeline
from pyspark.ml.feature import StringIndexer, VectorAssembler, OneHotEncoder
from pyspark.ml.feature import StandardScaler, Imputer

label = "bad_loan"
categoricalColumns = ["term", "home_ownership", "purpose", "addr_state",
                "verification_status","application_type"]

numericalColumns = ["loan_amnt","emp_length", "annual_inc","dti",
            "delinq_2yrs","revol_util","total_acc",
            "credit_length_in_years"]

categoricalColumnsclassVec = [c + "classVec" for c in categoricalColumns]

stages = []

for categoricalColumn in categoricalColumns:
  ## Category Indexing with StringIndexer
  stringIndexer = StringIndexer(inputCol=categoricalColumn, outputCol = categoricalColumn+"Index").setHandleInvalid("skip")
  ## Use OneHotEncoder to convert categorical variables into binary SparseVectors
  encoder = OneHotEncoder(inputCol=categoricalColumn+"Index", outputCol=categoricalColumn+"classVec")
  
  ## Add stages
  stages += [stringIndexer, encoder]

## Convert label into label indices using the StringIndexer
label_stringIndexer = StringIndexer(inputCol = label, outputCol = "label").setHandleInvalid("skip")
stages += [label_stringIndexer]

assemblerInputs = categoricalColumnsclassVec + numericalColumns
assembler = VectorAssembler(inputCols = assemblerInputs, outputCol="features").setHandleInvalid("skip")
stages += [assembler]

scaler = StandardScaler(inputCol="features",
                        outputCol="scaledFeatures",
                        withStd=True,
                        withMean=True)
stages += [scaler]

prepPipeline = Pipeline().setStages(stages)
pipelineModel = prepPipeline.fit(loan_stats)
dataset = pipelineModel.transform(loan_stats)

# display(dataset)

In [13]:
data_train = dataset.filter(dataset.issue_year <= 2015).cache()
data_test = dataset.filter(dataset.issue_year > 2015).cache()

print(str(data_train.count()))
print(str(data_test.count()))

783378
482410

In [14]:
from pyspark.ml.classification import LogisticRegression
from pyspark.ml.evaluation import BinaryClassificationEvaluator
from pyspark.ml.tuning import CrossValidator, ParamGridBuilder

# Use logistic regression 
lr = LogisticRegression(maxIter=10, elasticNetParam=0.5, labelCol = "label", featuresCol = "scaledFeatures")

lrEvaluator = BinaryClassificationEvaluator(rawPredictionCol = "rawPrediction", metricName = "areaUnderPR")

# Build the parameter grid for model tuning
lrParamGrid = (ParamGridBuilder()
             .addGrid(lr.regParam, [0.01, 0.1, 0.5])
             .addGrid(lr.elasticNetParam, [0.0, 0.25, 0.5])
             .addGrid(lr.maxIter, [1, 5, 10])
             .build())

# Execute CrossValidator for model tuning
crossVal = CrossValidator(estimator=lr,
                          estimatorParamMaps=lrParamGrid,
                          evaluator=lrEvaluator,
                          numFolds=5)

# Train the tuned model and establish our best model
cvModel = crossVal.fit(data_train)
glm_model = cvModel.bestModel

lrPredictions = cvModel.transform(data_test)

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.

In [15]:
from pyspark.mllib.evaluation import BinaryClassificationMetrics
print('Accuracy:', lrEvaluator.evaluate(lrPredictions))
print('AUC:', BinaryClassificationMetrics(lrPredictions['label','prediction'].rdd).areaUnderROC)
print('PR:', BinaryClassificationMetrics(lrPredictions['label','prediction'].rdd).areaUnderPR)

Accuracy: 0.3495422449155088
/databricks/spark/python/pyspark/sql/context.py:119: DeprecationWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
 DeprecationWarning)
AUC: 0.6464941458411628
PR: 0.008102346864596448

In [16]:
# Find the expected profits with a given cutoff

display(lrPredictions)
lrEarnedProfit = lrPredictions.withColumn('earnedProfit',
                              (1-col('prediction'))*col('net')).select('bad_loan', 'prediction', 'net', 'earnedProfit')
display(lrEarnedProfit)

bad_loan prediction net earnedProfit false 0.0 11.58 11.58 false 0.0 13.31 13.31 false 0.0 693.31 693.31 false 0.0 4389.55 4389.55 false 0.0 3217.17 3217.17 false 0.0 2645.05 2645.05 false 0.0 131.61 131.61 false 0.0 467.36 467.36 false 0.0 746.49 746.49 false 0.0 50.64 50.64 false 0.0 41.61 41.61 true 0.0 -14571.37 -14571.37 true 0.0 -13130.27 -13130.27 false 0.0 2624.62 2624.62 false 0.0 2560.41 2560.41 false 0.0 1153.67 1153.67 false 0.0 32.9 32.9 false 0.0 1484.42 1484.42 false 0.0 4300.92 4300.92 false 0.0 69.12 69.12 false 0.0 855.12 855.12 true 0.0 -11742.47 -11742.47 true 0.0 -12031.49 -12031.49 false 0.0 149.07 149.07 false 0.0 1085.64 1085.64 false 0.0 3.97 3.97 true 0.0 -11595.45 -11595.45 true 0.0 -13030.58 -13030.58 false 0.0 17.7 17.7 false 0.0 91.16 91.16 true 0.0 -14561.29 -14561.29 false 0.0 285.95 285.95 false 0.0 383.47 383.47 false 0.0 1161.48 1161.48 false 0.0 178.99 178.99 true 0.0 -5774.41 -5774.41 false 0.0 1315.45 1315.45 true 0.0 -3886.61 -3886.61 false 0.0 165.96 165.96 false 0.0 1772.03 1772.03 false 0.0 35.17 35.17 false 0.0 175.42 175.42 false 0.0 268.52 268.52 false 0.0 117.25 117.25 false 0.0 724.75 724.75 true 0.0 -21735.02 -21735.02 false 0.0 1055.4 1055.4 false 0.0 1049.69 1049.69 true 0.0 -23212.49 -23212.49 false 0.0 265.7 265.7 false 1.0 596.53 0.0 false 0.0 390.22 390.22 false 0.0 97.51 97.51 false 0.0 883.38 883.38 false 0.0 257.32 257.32 false 1.0 104.82 0.0 false 0.0 1098.61 1098.61 false 0.0 844.58 844.58 false 0.0 1637.31 1637.31 false 0.0 629.65 629.65 false 0.0 847.0 847.0 false 0.0 780.85 780.85 false 0.0 334.74 334.74 false 0.0 722.93 722.93 false 0.0 415.66 415.66 false 0.0 683.47 683.47 false 0.0 389.18 389.18 false 0.0 826.11 826.11 false 0.0 2676.28 2676.28 false 0.0 357.83 357.83 false 0.0 220.96 220.96 true 0.0 -18664.97 -18664.97 false 0.0 318.41 318.41 false 0.0 628.35 628.35 true 0.0 -22436.7 -22436.7 false 0.0 602.91 602.91 false 0.0 9.81 9.81 true 0.0 -9870.04 -9870.04 true 0.0 -12664.42 -12664.42 false 0.0 1719.87 1719.87 false 0.0 650.07 650.07 false 0.0 193.79 193.79 false 0.0 242.65 242.65 false 0.0 576.43 576.43 false 0.0 1999.49 1999.49 true 0.0 -5176.54 -5176.54 false 0.0 1164.09 1164.09 false 0.0 27.27 27.27 false 0.0 542.65 542.65 false 0.0 1395.0 1395.0 false 0.0 3626.33 3626.33 true 1.0 -19155.22 -0.0 true 0.0 -5000.0 -5000.0 false 0.0 1716.51 1716.51 false 0.0 1885.09 1885.09 true 0.0 -5134.58 -5134.58 false 0.0 2358.69 2358.69 false 0.0 3420.61 3420.61 false 0.0 3288.62 3288.62 false 0.0 1137.78 1137.78 false 0.0 4456.08 4456.08 false 0.0 763.29 763.29 false 0.0 32.31 32.31 true 0.0 -9630.02 -9630.02 false 0.0 855.35 855.35 false 0.0 451.32 451.32 false 0.0 61.98 61.98 false 0.0 406.3 406.3 false 0.0 2460.39 2460.39 false 0.0 412.05 412.05 false 0.0 402.28 402.28 false 0.0 657.57 657.57 true 0.0 -23264.82 -23264.82 true 0.0 -31019.76 -31019.76 false 0.0 339.44 339.44 false 0.0 2197.56 2197.56 false 0.0 1792.35 1792.35 false 0.0 385.5 385.5 false 0.0 1955.76 1955.76 false 0.0 21.37 21.37 false 0.0 8.14 8.14 false 0.0 428.78 428.78 true 0.0 -25973.66 -25973.66 false 0.0 449.74 449.74 false 0.0 1432.75 1432.75 true 0.0 -21475.15 -21475.15 false 0.0 2956.09 2956.09 false 0.0 639.06 639.06 false 0.0 1639.26 1639.26 false 0.0 536.33 536.33 true 0.0 -15107.9 -15107.9 false 0.0 509.37 509.37 false 0.0 299.54 299.54 false 0.0 216.35 216.35 false 0.0 686.01 686.01 true 0.0 -15574.39 -15574.39 true 0.0 -8056.06 -8056.06 false 0.0 414.48 414.48 false 0.0 2847.63 2847.63 false 0.0 103.95 103.95 false 0.0 572.52 572.52 false 0.0 1022.01 1022.01 false 0.0 638.24 638.24 false 0.0 374.18 374.18 false 0.0 718.24 718.24 false 0.0 745.93 745.93 true 0.0 -31407.88 -31407.88 false 0.0 829.6 829.6 true 0.0 -3914.12 -3914.12 true 0.0 -17989.88 -17989.88 false 0.0 2442.01 2442.01 false 0.0 989.58 989.58 true 0.0 -947.06 -947.06 true 0.0 -20047.35 -20047.35 false 0.0 170.98 170.98 false 0.0 200.68 200.68 false 0.0 1189.15 1189.15 true 0.0 -8647.58 -8647.58 false 0.0 504.37 504.37 f

In [17]:
print('With this cutoff, earned profits will be', lrEarnedProfit.select('earnedProfit').groupBy().sum().collect()[0][0])

With this cutoff, earned profits will be -320820003.79000515

In [18]:
from pyspark.sql.types import *

## Function to extract probability from array
getProb = udf(lambda v:float(v[1]),FloatType())

## Select out the necessary columns
lrPredictionsProb = lrPredictions.select(col("id"),
                                          col("net"),
                                          col("label"),
                                          getProb(col("probability")).alias("probability"),
                                          col("prediction"))

In [19]:
headers = ['cutoff', 'AUPR', 'AUC', 'earnedProfit']
performanceDf = spark.createDataFrame([(0,0,0,0)], headers)

for cutoff in range(1, 25, 1):
  cutoff = (cutoff * 0.01)
  
  print('Testing cutoff = ', str(format(cutoff, '.2f')))
  lrPredictionsProbTemp = ( lrPredictionsProb.withColumn('predictionTest', when(col('probability') >= cutoff, 1)
                                                            .otherwise(0).cast(DoubleType()))
                                                .withColumn('earnedProfit',(1-col('predictionTest'))*col('net'))
                            )
  auprTemp = BinaryClassificationMetrics(lrPredictionsProbTemp['label', 'predictionTest'].rdd).areaUnderPR
  aucTemp = BinaryClassificationMetrics(lrPredictionsProbTemp['label', 'predictionTest'].rdd).areaUnderROC
  epTemp = lrPredictionsProbTemp.select('earnedProfit').groupBy().sum().collect()[0][0]
  print('\tAUPR:', auprTemp, '\tAUC:', aucTemp, '\tearnedProfit:', epTemp)
  performanceDfRow = spark.createDataFrame([(cutoff, auprTemp, aucTemp, epTemp)], headers)
  performanceDf = performanceDf.union(performanceDfRow)

display(performanceDf)

cutoff AUPR AUC earnedProfit 0.0 0.0 0.0 0.0 0.01 0.9997196319417081 0.5597470807996007 130025.59000000001 0.02 0.9992024129091485 0.5387577047970418 106737.85999999993 0.03 0.9988347597145261 0.5477010630453186 412884.1199999999 0.04 0.9980259004935301 0.5621563373945387 954115.8400000003 0.05 0.9953857959398722 0.5735188089951571 2076879.0799999982 0.06 0.9886914476809032 0.5790094144595652 4899455.450000009 0.07 0.974869520740484 0.5794844118918094 9083471.049999984 0.08 0.9526492668482978 0.5789968068276505 1.529336459000005E7 0.09 0.9214717686383911 0.5783888950596191 2.1517336449999996E7 0.1 0.8812454068516773 0.5771659034856031 2.504241042999988E7 0.11 0.8334329455168987 0.5764917198461142 2.7213402239999607E7 0.12 0.7816258373199647 0.5766893916733369 2.7148593209999725E7 0.13 0.7262331220009155 0.577076669953178 2.3518353449999742E7 0.14 0.6712608653572013 0.5780671068407127 1.884896564999936E7 0.15 0.6169548008676877 0.5789651700548393 1.033488831999896E7 0.16 0.5657739706189276 0.5799853857211907 271088.85999911465 0.17 0.5180022373969282 0.5816841095564123 -1.0314290150000378E7 0.18 0.47537143458470715 0.5838157330613438 -2.017330569000084E7 0.19 0.43527371408791343 0.5854474583547936 -3.1410254420000724E7 0.2 0.39863231619137685 0.5865627808406487 -4.35899097100007E7 0.21 0.36656315803911527 0.5882987932182572 -5.4487980690000705E7 0.22 0.3387363505878759 0.5908721667124802 -6.481171092000031E7 0.23 0.3132144922045596 0.5934969577074465 -7.576832575999986E7 0.24 0.28999175730286425 0.5962815151764793 -8.628953850000004E7

In [20]:
display(performanceDf)

cutoff AUPR AUC earnedProfit 0.0 0.0 0.0 0.0 0.01 0.9997196319417081 0.5597470807996007 130025.59000000001 0.02 0.9992024129091485 0.5387577047970418 106737.85999999993 0.03 0.9988347597145261 0.5477010630453186 412884.1199999999 0.04 0.9980259004935301 0.5621563373945387 954115.8400000003 0.05 0.9953857959398722 0.5735188089951571 2076879.0799999982 0.06 0.9886914476809032 0.5790094144595652 4899455.450000009 0.07 0.974869520740484 0.5794844118918094 9083471.049999984 0.08 0.9526492668482978 0.5789968068276505 1.529336459000005E7 0.09 0.9214717686383911 0.5783888950596191 2.1517336449999996E7 0.1 0.8812454068516773 0.5771659034856031 2.504241042999988E7 0.11 0.8334329455168987 0.5764917198461142 2.7213402239999607E7 0.12 0.7816258373199647 0.5766893916733369 2.7148593209999725E7 0.13 0.7262331220009155 0.577076669953178 2.3518353449999742E7 0.14 0.6712608653572013 0.5780671068407127 1.884896564999936E7 0.15 0.6169548008676877 0.5789651700548393 1.033488831999896E7 0.16 0.5657739706189276 0.5799853857211907 271088.85999911465 0.17 0.5180022373969282 0.5816841095564123 -1.0314290150000378E7 0.18 0.47537143458470715 0.5838157330613438 -2.017330569000084E7 0.19 0.43527371408791343 0.5854474583547936 -3.1410254420000724E7 0.2 0.39863231619137685 0.5865627808406487 -4.35899097100007E7 0.21 0.36656315803911527 0.5882987932182572 -5.4487980690000705E7 0.22 0.3387363505878759 0.5908721667124802 -6.481171092000031E7 0.23 0.3132144922045596 0.5934969577074465 -7.576832575999986E7 0.24 0.28999175730286425 0.5962815151764793 -8.628953850000004E7

In [21]:
display(performanceDf)

cutoff AUPR AUC earnedProfit 0.0 0.0 0.0 0.0 0.01 0.9997196319417081 0.5597470807996007 130025.59000000001 0.02 0.9992024129091485 0.5387577047970418 106737.85999999993 0.03 0.9988347597145261 0.5477010630453186 412884.1199999999 0.04 0.9980259004935301 0.5621563373945387 954115.8400000003 0.05 0.9953857959398722 0.5735188089951571 2076879.0799999982 0.06 0.9886914476809032 0.5790094144595652 4899455.450000009 0.07 0.974869520740484 0.5794844118918094 9083471.049999984 0.08 0.9526492668482978 0.5789968068276505 1.529336459000005E7 0.09 0.9214717686383911 0.5783888950596191 2.1517336449999996E7 0.1 0.8812454068516773 0.5771659034856031 2.504241042999988E7 0.11 0.8334329455168987 0.5764917198461142 2.7213402239999607E7 0.12 0.7816258373199647 0.5766893916733369 2.7148593209999725E7 0.13 0.7262331220009155 0.577076669953178 2.3518353449999742E7 0.14 0.6712608653572013 0.5780671068407127 1.884896564999936E7 0.15 0.6169548008676877 0.5789651700548393 1.033488831999896E7 0.16 0.5657739706189276 0.5799853857211907 271088.85999911465 0.17 0.5180022373969282 0.5816841095564123 -1.0314290150000378E7 0.18 0.47537143458470715 0.5838157330613438 -2.017330569000084E7 0.19 0.43527371408791343 0.5854474583547936 -3.1410254420000724E7 0.2 0.39863231619137685 0.5865627808406487 -4.35899097100007E7 0.21 0.36656315803911527 0.5882987932182572 -5.4487980690000705E7 0.22 0.3387363505878759 0.5908721667124802 -6.481171092000031E7 0.23 0.3132144922045596 0.5934969577074465 -7.576832575999986E7 0.24 0.28999175730286425 0.5962815151764793 -8.628953850000004E7

In [22]:
print("\nConfusion Matrix when maximizing AUC: \n")

for model in ["lrPredictions"]:
    df = globals()[model]
    
    tp = df[(df.label == 1) & (df.prediction == 1)].count()
    tn = df[(df.label == 0) & (df.prediction == 0)].count()
    fp = df[(df.label == 0) & (df.prediction == 1)].count()
    fn = df[(df.label == 1) & (df.prediction == 0)].count()
    a = ((tp + tn)/df.count())
    
    if(tp + fn == 0.0):
        r = 0.0
        p = float(tp) / (tp + fp)
    elif(tp + fp == 0.0):
        r = float(tp) / (tp + fn)
        p = 0.0
    else:
        r = float(tp) / (tp + fn)
        p = float(tp) / (tp + fp)
    
    if(p + r == 0):
        f1 = 0
    else:
        f1 = 2 * ((p * r)/(p + r))
    
    print("Model:", model)
    print("True Positives:", tp)
    print("True Negatives:", tn)
    print("False Positives:", fp)
    print("False Negatives:", fn)
    print("Total:", df.count())
    print("Accuracy:", a)
    print("Recall:", r)
    print("Precision: ", p)
    print("F1 score:", f1)
    print('AUC:', BinaryClassificationMetrics(df['label','prediction'].rdd).areaUnderROC)
print("\n")

Confusion Matrix when maximizing AUC: 

Model: lrPredictions
True Positives: 991
True Negatives: 376308
False Positives: 953
False Negatives: 104158
Total: 482410
Accuracy: 0.782112725689766
Recall: 0.009424721110043843
Precision: 0.5097736625514403
F1 score: 0.01850727872036454
AUC: 0.6464941458411628

In [23]:
print("\nConfusion Matrix when maximizing profit: \n")

cutoffBest = 0.11
lrPredictionsProbBest = ( lrPredictionsProb.withColumn('predictionBest', when(col('probability') >= cutoffBest, 1)
                                                            .otherwise(0).cast(DoubleType()))
                                                .withColumn('earnedProfit',(1-col('predictionBest'))*col('net'))
                            )

for model in ["lrPredictionsProbBest"]:
    df = globals()[model]
    
    tp = df[(df.label == 1) & (df.predictionBest == 1)].count()
    tn = df[(df.label == 0) & (df.predictionBest == 0)].count()
    fp = df[(df.label == 0) & (df.predictionBest == 1)].count()
    fn = df[(df.label == 1) & (df.predictionBest == 0)].count()
    a = ((tp + tn)/df.count())
    
    if(tp + fn == 0.0):
        r = 0.0
        p = float(tp) / (tp + fp)
    elif(tp + fp == 0.0):
        r = float(tp) / (tp + fn)
        p = 0.0
    else:
        r = float(tp) / (tp + fn)
        p = float(tp) / (tp + fp)
    
    if(p + r == 0):
        f1 = 0
    else:
        f1 = 2 * ((p * r)/(p + r))
    
    print("Model:", model)
    print("True Positives:", tp)
    print("True Negatives:", tn)
    print("False Positives:", fp)
    print("False Negatives:", fn)
    print("Total:", df.count())
    print("Accuracy:", a)
    print("Recall:", r)
    print("Precision: ", p)
    print("F1 score:", f1)
    print('AUC:', BinaryClassificationMetrics(df['label','predictionBest'].rdd).areaUnderROC)
print("\n")

Confusion Matrix when maximizing profit: 

Model: lrPredictionsProbBest
True Positives: 92768
True Negatives: 107736
False Positives: 269525
False Negatives: 12381
Total: 482410
Accuracy: 0.415629858419187
Recall: 0.8822528031650325
Precision: 0.25605794205242716
F1 score: 0.39691769246238034
AUC: 0.5764917198461142

In [24]:
from pyspark.ml.classification import GBTClassifier

# Discussion on GBT parameters: https://medium.com/all-things-ai/in-depth-parameter-tuning-for-gradient-boosting-3363992e9bae

# Define a GBT model.
gbt = GBTClassifier(featuresCol = "scaledFeatures",
                    labelCol = "label",
                    lossType = "logistic",
                    maxBins = 52,
                    maxIter = 20,
                    maxDepth = 5)

gbtEvaluator = BinaryClassificationEvaluator(rawPredictionCol = "rawPrediction", metricName = "areaUnderROC")

# Build the parameter grid for model tuning
gbtParamGrid = ( ParamGridBuilder()
               .addGrid(gbt.maxBins, [52, 62])
               .addGrid(gbt.maxIter, [20, 30])
               .addGrid(gbt.maxDepth, [5, 8])
               .build() )

# Execute CrossValidator for model tuning
gbtCrossVal = CrossValidator(estimator = gbt,
                          estimatorParamMaps = gbtParamGrid,
                          evaluator = gbtEvaluator,
                          numFolds = 5)

# Train the tuned model and establish our best model
gbtCvModel = gbtCrossVal.fit(data_train)
gbtModel = gbtCvModel.bestModel
gbtPredictions = gbtCvModel.transform(data_test)

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.

In [25]:
# from pyspark.mllib.evaluation import BinaryClassificationMetrics

print('Accuracy:', gbtEvaluator.evaluate(gbtPredictions))
print('AUC:', BinaryClassificationMetrics(gbtPredictions['label','prediction'].rdd).areaUnderROC)
print('PR:', BinaryClassificationMetrics(gbtPredictions['label','prediction'].rdd).areaUnderPR)

Accuracy: 0.6665857883573562
AUC: 0.6330554257651437
PR: 0.021544371049691625

In [26]:
display(gbtPredictions)
gbtProfits =gbtPredictions.withColumn('earnedProfit',
                              (1-col('prediction'))*col('net')).select('net', 'bad_loan', 'prediction', 'earnedProfit')
display(gbtProfits)

net bad_loan prediction earnedProfit 11.58 false 0.0 11.58 13.31 false 0.0 13.31 693.31 false 0.0 693.31 4389.55 false 0.0 4389.55 3217.17 false 0.0 3217.17 2645.05 false 0.0 2645.05 131.61 false 0.0 131.61 467.36 false 0.0 467.36 746.49 false 0.0 746.49 50.64 false 0.0 50.64 41.61 false 0.0 41.61 -14571.37 true 0.0 -14571.37 -13130.27 true 0.0 -13130.27 2624.62 false 0.0 2624.62 2560.41 false 0.0 2560.41 1153.67 false 0.0 1153.67 32.9 false 0.0 32.9 1484.42 false 0.0 1484.42 4300.92 false 0.0 4300.92 69.12 false 0.0 69.12 855.12 false 0.0 855.12 -11742.47 true 0.0 -11742.47 -12031.49 true 0.0 -12031.49 149.07 false 0.0 149.07 1085.64 false 0.0 1085.64 3.97 false 0.0 3.97 -11595.45 true 0.0 -11595.45 -13030.58 true 0.0 -13030.58 17.7 false 0.0 17.7 91.16 false 0.0 91.16 -14561.29 true 0.0 -14561.29 285.95 false 0.0 285.95 383.47 false 0.0 383.47 1161.48 false 0.0 1161.48 178.99 false 0.0 178.99 -5774.41 true 0.0 -5774.41 1315.45 false 0.0 1315.45 -3886.61 true 0.0 -3886.61 165.96 false 0.0 165.96 1772.03 false 0.0 1772.03 35.17 false 0.0 35.17 175.42 false 0.0 175.42 268.52 false 0.0 268.52 117.25 false 0.0 117.25 724.75 false 1.0 0.0 -21735.02 true 0.0 -21735.02 1055.4 false 0.0 1055.4 1049.69 false 0.0 1049.69 -23212.49 true 0.0 -23212.49 265.7 false 0.0 265.7 596.53 false 1.0 0.0 390.22 false 0.0 390.22 97.51 false 0.0 97.51 883.38 false 0.0 883.38 257.32 false 0.0 257.32 104.82 false 0.0 104.82 1098.61 false 0.0 1098.61 844.58 false 0.0 844.58 1637.31 false 0.0 1637.31 629.65 false 0.0 629.65 847.0 false 0.0 847.0 780.85 false 0.0 780.85 334.74 false 0.0 334.74 722.93 false 0.0 722.93 415.66 false 0.0 415.66 683.47 false 0.0 683.47 389.18 false 0.0 389.18 826.11 false 0.0 826.11 2676.28 false 0.0 2676.28 357.83 false 0.0 357.83 220.96 false 0.0 220.96 -18664.97 true 0.0 -18664.97 318.41 false 0.0 318.41 628.35 false 0.0 628.35 -22436.7 true 0.0 -22436.7 602.91 false 0.0 602.91 9.81 false 0.0 9.81 -9870.04 true 0.0 -9870.04 -12664.42 true 0.0 -12664.42 1719.87 false 0.0 1719.87 650.07 false 1.0 0.0 193.79 false 0.0 193.79 242.65 false 0.0 242.65 576.43 false 0.0 576.43 1999.49 false 0.0 1999.49 -5176.54 true 0.0 -5176.54 1164.09 false 1.0 0.0 27.27 false 0.0 27.27 542.65 false 0.0 542.65 1395.0 false 0.0 1395.0 3626.33 false 0.0 3626.33 -19155.22 true 0.0 -19155.22 -5000.0 true 0.0 -5000.0 1716.51 false 0.0 1716.51 1885.09 false 0.0 1885.09 -5134.58 true 0.0 -5134.58 2358.69 false 0.0 2358.69 3420.61 false 0.0 3420.61 3288.62 false 0.0 3288.62 1137.78 false 0.0 1137.78 4456.08 false 0.0 4456.08 763.29 false 0.0 763.29 32.31 false 0.0 32.31 -9630.02 true 0.0 -9630.02 855.35 false 0.0 855.35 451.32 false 0.0 451.32 61.98 false 0.0 61.98 406.3 false 0.0 406.3 2460.39 false 0.0 2460.39 412.05 false 0.0 412.05 402.28 false 0.0 402.28 657.57 false 0.0 657.57 -23264.82 true 0.0 -23264.82 -31019.76 true 0.0 -31019.76 339.44 false 0.0 339.44 2197.56 false 0.0 2197.56 1792.35 false 0.0 1792.35 385.5 false 0.0 385.5 1955.76 false 0.0 1955.76 21.37 false 0.0 21.37 8.14 false 0.0 8.14 428.78 false 0.0 428.78 -25973.66 true 0.0 -25973.66 449.74 false 0.0 449.74 1432.75 false 0.0 1432.75 -21475.15 true 0.0 -21475.15 2956.09 false 0.0 2956.09 639.06 false 0.0 639.06 1639.26 false 0.0 1639.26 536.33 false 0.0 536.33 -15107.9 true 0.0 -15107.9 509.37 false 0.0 509.37 299.54 false 0.0 299.54 216.35 false 0.0 216.35 686.01 false 0.0 686.01 -15574.39 true 0.0 -15574.39 -8056.06 true 0.0 -8056.06 414.48 false 0.0 414.48 2847.63 false 0.0 2847.63 103.95 false 0.0 103.95 572.52 false 0.0 572.52 1022.01 false 0.0 1022.01 638.24 false 0.0 638.24 374.18 false 0.0 374.18 718.24 false 0.0 718.24 745.93 false 0.0 745.93 -31407.88 true 0.0 -31407.88 829.6 false 0.0 829.6 -3914.12 true 0.0 -3914.12 -17989.88 true 0.0 -17989.88 2442.01 false 0.0 2442.01 989.58 false 0.0 989.58 -947.06 true 0.0 -947.06 -20047.35 true 0.0 -20047.35 170.98 false 0.0 170.98 200.68 false 0.0 200.68 1189.15 false 0.0 1189.15 -8647.58 true 0.0 -8647.58 504.37 false 0.0 504.37 158

In [27]:
print('With this cutoff, earned profits will be', gbtProfits.select('earnedProfit').groupBy().sum().collect()[0][0])

With this cutoff, earned profits will be -306475513.650005

In [28]:
from pyspark.sql.types import *

## Function to extract probability from array
getProb = udf(lambda v:float(v[1]),FloatType())

## Select out the necessary columns
gbtPredictionsProb = gbtPredictions.select(col("id"),
                                          col("net"),
                                          col("label"),
                                          getProb(col("probability")).alias("probability"),
                                          col("prediction"))

In [29]:
headers = ['cutoff', 'AUPR', 'AUC', 'earnedProfit']
performanceDf = spark.createDataFrame([(0,0,0,0)], headers)

for cutoff in range(1, 25, 1):
  cutoff = (cutoff * 0.01)
  
  print('Testing cutoff = ', str(format(cutoff, '.2f')))
  gbtPredictionsProbTemp = ( gbtPredictionsProb.withColumn('predictionTest', when(col('probability') >= cutoff, 1)
                                                            .otherwise(0).cast(DoubleType()))
                                                .withColumn('earnedProfit',(1-col('predictionTest'))*col('net'))
                            )
  auprTemp = BinaryClassificationMetrics(gbtPredictionsProbTemp['label', 'predictionTest'].rdd).areaUnderPR
  aucTemp = BinaryClassificationMetrics(gbtPredictionsProbTemp['label', 'predictionTest'].rdd).areaUnderROC
  epTemp = gbtPredictionsProbTemp.select('earnedProfit').groupBy().sum().collect()[0][0]
  print('\tAUPR:', auprTemp, '\tAUC:', aucTemp, '\tearnedProfit:', epTemp)
  performanceDfRow = spark.createDataFrame([(cutoff, auprTemp, aucTemp, epTemp)], headers)
  performanceDf = performanceDf.union(performanceDfRow)

# display(performanceDf)

cutoff AUPR AUC earnedProfit 0.0 0.0 0.0 0.0 0.01 1.0 1.0 0.0 0.02 1.0 1.0 0.0 0.03 1.0 1.0 0.0 0.04 1.0 1.0 0.0 0.05 0.9999212623809084 0.6034467665542471 39118.840000000004 0.06 0.9955440866860282 0.5923461208386669 1946620.349999998 0.07 0.9818129300806594 0.5886308815063744 7786211.770000007 0.08 0.9582180962228894 0.5847548120469565 1.5997690239999983E7 0.09 0.9264859614561203 0.5812839957268314 2.3467254909999914E7 0.1 0.8861463671098337 0.5795085522088567 3.0005905809999757E7 0.11 0.8367173228614866 0.5786821502241283 3.413620829999949E7 0.12 0.7832081543717395 0.5788191945936121 3.450061270999976E7 0.13 0.7267673240336957 0.5788652855158293 3.1249799029999536E7 0.14 0.6711793283524816 0.5798195445106205 2.655907133999958E7 0.15 0.6159973059568995 0.5810608529045796 1.8752136549999468E7 0.16 0.5618619405429823 0.5819275626697975 6667304.53999953 0.17 0.5147702923180547 0.5832802243779533 -4008717.3800000474 0.18 0.47085263982203057 0.5848397138236399 -1.457877202000024E7 0.19 0.43085091475157017 0.5869962627784717 -2.5959590190000925E7 0.2 0.39411347710029165 0.589150378318664 -3.7072322280000925E7 0.21 0.36020190615771286 0.5911728261755264 -4.893859313000117E7 0.22 0.33159733364300337 0.593177559041705 -6.0221470420000374E7 0.23 0.30687963270697094 0.5951910645332463 -7.06075473200001E7 0.24 0.28513302955274494 0.597244401372691 -8.089343221999976E7

In [30]:
display(performanceDf)

cutoff AUPR AUC earnedProfit 0.0 0.0 0.0 0.0 0.01 1.0 1.0 0.0 0.02 1.0 1.0 0.0 0.03 1.0 1.0 0.0 0.04 1.0 1.0 0.0 0.05 0.9999212623809084 0.6034467665542471 39118.840000000004 0.06 0.9955440866860282 0.5923461208386669 1946620.349999998 0.07 0.9818129300806594 0.5886308815063744 7786211.770000007 0.08 0.9582180962228894 0.5847548120469565 1.5997690239999983E7 0.09 0.9264859614561203 0.5812839957268314 2.3467254909999914E7 0.1 0.8861463671098337 0.5795085522088567 3.0005905809999757E7 0.11 0.8367173228614866 0.5786821502241283 3.413620829999949E7 0.12 0.7832081543717395 0.5788191945936121 3.450061270999976E7 0.13 0.7267673240336957 0.5788652855158293 3.1249799029999536E7 0.14 0.6711793283524816 0.5798195445106205 2.655907133999958E7 0.15 0.6159973059568995 0.5810608529045796 1.8752136549999468E7 0.16 0.5618619405429823 0.5819275626697975 6667304.53999953 0.17 0.5147702923180547 0.5832802243779533 -4008717.3800000474 0.18 0.47085263982203057 0.5848397138236399 -1.457877202000024E7 0.19 0.43085091475157017 0.5869962627784717 -2.5959590190000925E7 0.2 0.39411347710029165 0.589150378318664 -3.7072322280000925E7 0.21 0.36020190615771286 0.5911728261755264 -4.893859313000117E7 0.22 0.33159733364300337 0.593177559041705 -6.0221470420000374E7 0.23 0.30687963270697094 0.5951910645332463 -7.06075473200001E7 0.24 0.28513302955274494 0.597244401372691 -8.089343221999976E7

In [31]:
display(performanceDf)

cutoff AUPR AUC earnedProfit 0.0 0.0 0.0 0.0 0.01 1.0 1.0 0.0 0.02 1.0 1.0 0.0 0.03 1.0 1.0 0.0 0.04 1.0 1.0 0.0 0.05 0.9999212623809084 0.6034467665542471 39118.840000000004 0.06 0.9955440866860282 0.5923461208386669 1946620.349999998 0.07 0.9818129300806594 0.5886308815063744 7786211.770000007 0.08 0.9582180962228894 0.5847548120469565 1.5997690239999983E7 0.09 0.9264859614561203 0.5812839957268314 2.3467254909999914E7 0.1 0.8861463671098337 0.5795085522088567 3.0005905809999757E7 0.11 0.8367173228614866 0.5786821502241283 3.413620829999949E7 0.12 0.7832081543717395 0.5788191945936121 3.450061270999976E7 0.13 0.7267673240336957 0.5788652855158293 3.1249799029999536E7 0.14 0.6711793283524816 0.5798195445106205 2.655907133999958E7 0.15 0.6159973059568995 0.5810608529045796 1.8752136549999468E7 0.16 0.5618619405429823 0.5819275626697975 6667304.53999953 0.17 0.5147702923180547 0.5832802243779533 -4008717.3800000474 0.18 0.47085263982203057 0.5848397138236399 -1.457877202000024E7 0.19 0.43085091475157017 0.5869962627784717 -2.5959590190000925E7 0.2 0.39411347710029165 0.589150378318664 -3.7072322280000925E7 0.21 0.36020190615771286 0.5911728261755264 -4.893859313000117E7 0.22 0.33159733364300337 0.593177559041705 -6.0221470420000374E7 0.23 0.30687963270697094 0.5951910645332463 -7.06075473200001E7 0.24 0.28513302955274494 0.597244401372691 -8.089343221999976E7

In [32]:
print("Confusion Matrix when maximizing profit: \n")

cutoffBest = 0.12
gbtPredictionsProbBest = ( gbtPredictionsProb.withColumn('predictionBest', when(col('probability') >= cutoffBest, 1)
                                                            .otherwise(0).cast(DoubleType()))
                                                .withColumn('earnedProfit',(1-col('predictionBest'))*col('net'))
                            )

for model in ["gbtPredictionsProbBest"]:
    df = globals()[model]
    
    tp = df[(df.label == 1) & (df.predictionBest == 1)].count()
    tn = df[(df.label == 0) & (df.predictionBest == 0)].count()
    fp = df[(df.label == 0) & (df.predictionBest == 1)].count()
    fn = df[(df.label == 1) & (df.predictionBest == 0)].count()
    a = ((tp + tn)/df.count())
    
    if(tp + fn == 0.0):
        r = 0.0
        p = float(tp) / (tp + fp)
    elif(tp + fp == 0.0):
        r = float(tp) / (tp + fn)
        p = 0.0
    else:
        r = float(tp) / (tp + fn)
        p = float(tp) / (tp + fp)
    
    if(p + r == 0):
        f1 = 0
    else:
        f1 = 2 * ((p * r)/(p + r))
    
    print("Model:", model)
    print("True Positives:", tp)
    print("True Negatives:", tn)
    print("False Positives:", fp)
    print("False Negatives:", fn)
    print("Total:", df.count())
    print("Accuracy:", a)
    print("Recall:", r)
    print("Precision: ", p)
    print("F1 score:", f1)
    print('AUC:', BinaryClassificationMetrics(df['label','predictionBest'].rdd).areaUnderROC)
print("\n")

Confusion Matrix when maximizing profit: 

Model: gbtPredictionsProbBest
True Positives: 88370
True Negatives: 135593
False Positives: 241668
False Negatives: 16779
Total: 482410
Accuracy: 0.4642586181878485
Recall: 0.8404264424768662
Precision: 0.2677570461583212
F1 score: 0.406124263822219
AUC: 0.5788191945936121

In [33]:
import pandas as pd

def ExtractFeatureImportance(featureImp, dataset, featuresCol):
    list_extract = []
    for i in dataset.schema[featuresCol].metadata["ml_attr"]["attrs"]:
        list_extract = list_extract + dataset.schema[featuresCol].metadata["ml_attr"]["attrs"][i]
    varlist = pd.DataFrame(list_extract)
    varlist['score'] = varlist['idx'].apply(lambda x: featureImp[x])
    return(varlist.sort_values('score', ascending = False))
  
  
# ExtractFeatureImportance(model.stages[-1].featureImportances, dataset, "features")
datasetFI = ExtractFeatureImportance(gbtModel.featureImportances, data_train, "features")
datasetFI = sqlContext.createDataFrame(datasetFI)
display(datasetFI)

idx name score 0 termclassVec_ 36 months 0.18150416271426023 73 annual_inc 0.10204798486926116 74 dti 0.08459121009360428 78 credit_length_in_years 0.0841705726749196 76 revol_util 0.08277240385603789 71 loan_amnt 0.07744408757974895 77 total_acc 0.05344323105126992 75 delinq_2yrs 0.040242549261228416 72 emp_length 0.034987714526616566 7 purposeclassVec_credit_card 0.025625158537923548 1 home_ownershipclassVec_MORTGAGE 0.022056799598115236 69 verification_statusclassVec_Verified 0.021615609617657586 2 home_ownershipclassVec_RENT 0.018633677509220778 12 purposeclassVec_small_business 0.013676344553885557 21 addr_stateclassVec_NY 0.008029693823008995 34 addr_stateclassVec_CO 0.007601805672092494 44 addr_stateclassVec_OR 0.006801368397177547 6 purposeclassVec_debt_consolidation 0.006741405796419351 35 addr_stateclassVec_WA 0.005905012159376152 9 purposeclassVec_other 0.005875695017845634 22 addr_stateclassVec_FL 0.005655344745225093 19 addr_stateclassVec_CA 0.005264048384524394 3 home_ownershipclassVec_OWN 0.004474253051328854 40 addr_stateclassVec_NV 0.004459478537280847 24 addr_stateclassVec_NJ 0.004157495335766724 14 purposeclassVec_moving 0.003915460529634506 54 addr_stateclassVec_MS 0.0038922442319818716 46 addr_stateclassVec_LA 0.0038862533591981934 45 addr_stateclassVec_SC 0.0036745626272402104 16 purposeclassVec_house 0.003553206748210828 20 addr_stateclassVec_TX 0.0033439205002094644 48 addr_stateclassVec_OK 0.0033245017481075808 50 addr_stateclassVec_AR 0.002928685103084848 11 purposeclassVec_medical 0.0028605033427798383 43 addr_stateclassVec_AL 0.002741740510798602 8 purposeclassVec_home_improvement 0.002619335860256146 55 addr_stateclassVec_NH 0.002586861161334586 32 addr_stateclassVec_MD 0.0025170372344664057 39 addr_stateclassVec_TN 0.002418984703490011 10 purposeclassVec_major_purchase 0.002371683509356211 49 addr_stateclassVec_KS 0.002313298723596215 17 purposeclassVec_wedding 0.0022031079587522865 27 addr_stateclassVec_GA 0.002169757986595163 15 purposeclassVec_vacation 0.0019106021031911349 23 addr_stateclassVec_IL 0.001908348655871891 37 addr_stateclassVec_IN 0.0019063875211404872 25 addr_stateclassVec_PA 0.0018254274022028985 60 addr_stateclassVec_NE 0.0017554349372920126 18 purposeclassVec_renewable_energy 0.0017306350362887716 13 purposeclassVec_car 0.0016485556104005674 26 addr_stateclassVec_OH 0.0015318036516132362 47 addr_stateclassVec_KY 0.001517917129739354 29 addr_stateclassVec_NC 0.0014731302703984428 51 addr_stateclassVec_UT 0.0014253235119956506 36 addr_stateclassVec_MN 0.0013864657869733052 30 addr_stateclassVec_MI 0.0013816649180675234 64 addr_stateclassVec_SD 0.0013796182310426865 57 addr_stateclassVec_WV 0.0013541615689542463 31 addr_stateclassVec_AZ 0.0012330786529272098 33 addr_stateclassVec_MA 0.001185063441819271 61 addr_stateclassVec_DC 0.0011515148600289074 52 addr_stateclassVec_NM 9.980210298908198E-4 63 addr_stateclassVec_WY 9.972501843403623E-4 62 addr_stateclassVec_AK 9.558758432624153E-4 58 addr_stateclassVec_MT 9.555327623053904E-4 41 addr_stateclassVec_CT 9.026703347022984E-4 65 addr_stateclassVec_VT 8.714111603459703E-4 42 addr_stateclassVec_WI 8.176247368228642E-4 56 addr_stateclassVec_RI 6.919939780448281E-4 53 addr_stateclassVec_HI 6.778833227007673E-4 59 addr_stateclassVec_DE 6.597670868236624E-4 38 addr_stateclassVec_MO 5.696865904260424E-4 70 application_typeclassVec_Individual 5.491483043768691E-4 28 addr_stateclassVec_VA 4.813366357564844E-4 68 addr_stateclassVec_ND 3.6958333926871326E-4 66 addr_stateclassVec_ME 3.3601336099616934E-4 5 home_ownershipclassVec_OTHER 3.138029408919639E-4 67 addr_stateclassVec_ID 4.9011896207762925E-5 4 home_ownershipclassVec_ANY 0.0

In [34]:
display(datasetFI.select("*").toPandas()[0:10])

idx name score 0 termclassVec_ 36 months 0.18150416271426023 73 annual_inc 0.10204798486926116 74 dti 0.08459121009360428 78 credit_length_in_years 0.0841705726749196 76 revol_util 0.08277240385603789 71 loan_amnt 0.07744408757974895 77 total_acc 0.05344323105126992 75 delinq_2yrs 0.040242549261228416 72 emp_length 0.034987714526616566 7 purposeclassVec_credit_card 0.025625158537923548